In [21]:
# Importing the required libraries

import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
from sklearn.metrics import mean_absolute_error
import joblib
import os

In [3]:
# Creating our X_train array 
import csv

Euler_KAM = []
for file_index in range(1, 20):
    if (file_index==6):
        continue
    with open(f"IPF\IPF_Final_{file_index}.csv", "r") as file:
        contents = csv.DictReader(file, delimiter=",")
        Euler_at_fixed_strain = []
        for row in contents:
            Euler_at_fixed_strain.append(float(row["Phi2"])) 
        Euler_KAM.append(Euler_at_fixed_strain)
        
X_train = []
for j in range(len(Euler_KAM[1])):
    y_values = np.array([i[j] for i in Euler_KAM]) 
    X_train.append(y_values)

# Reshape for RNN input
# As we always have a 3-D array as an input to a LSTM network
# The first dimension represents batch size
# The second dimension represents time steps
# The third dimension represents the number of units in one input sequence


In [4]:
np.shape(X_train)

10248

In [5]:
# Creating our Y _train array
import pandas as pd
Y_train = []
df = pd.read_csv("IPF\IPF_Final_20.csv")
for i in range(len(df['Phi2'])):
    Y_train.append(df['Phi2'].iloc[i])

In [6]:
np.shape(Y_train)

(10248,)

In [8]:
# Splitting our data into training-testing batches
# and adjusting their shapes according to the model requirements
x_train, x_test, y_train, y_test = train_test_split(X_train, Y_train, test_size=0.3, random_state=42)

In [9]:
x_train = np.array(x_train)
x_train = x_train.reshape((x_train.shape[0], x_train.shape[1], 1))
y_train = np.array(y_train)
y_train = y_train.reshape((y_train.shape[0], 1,1))

In [10]:
x_test = np.array(x_test)
x_test = x_test.reshape((x_test.shape[0], x_test.shape[1], 1))
y_test = np.array(y_test)
y_test = y_test.reshape((y_test.shape[0], 1,1))

(7173,)

In [11]:
print(np.shape(x_train))
print(np.shape(y_train))
print(np.shape(x_test))
print(np.shape(y_test))

In [12]:
# Initialization and training of our model

import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error

# Initializing the model here

model = Sequential()
model.add(LSTM(32, input_shape=(18, 1), return_sequences=True))
model.add(LSTM(32, return_sequences=False))
model.add(Dense(1))

# Compile the model
model.compile(optimizer='adam', loss='mean_squared_error')

# Print model summary
model.summary()

# Train the model
history = model.fit(x_train, y_train, epochs=100, validation_data=(x_test, y_test))

# Save the model
model.save("Tension_Phi2_lstm.h5")

In [22]:
# Defining a function that would predict the data for a given Euler Angle ("Euler") and a given file index ("to_predict")
import pandas as pd
from keras.models import load_model
import csv

def predictions(to_predict, Euler):
    Euler_KAM = []
    for file_index in range(1, 20):
        if (file_index==6):
            continue
        with open(fr"IPF\IPF_Final_{file_index}.csv", "r") as file:
            contents = csv.DictReader(file, delimiter=",")
            Euler_at_fixed_strain = []
            for row in contents:
                Euler_at_fixed_strain.append(float(row[f"Phi{Euler}"])) 
            Euler_KAM.append(Euler_at_fixed_strain)

    X_train = []
    for j in range(len(Euler_KAM[1])):
        y_values = np.array([i[j] for i in Euler_KAM]) 
        X_train.append(y_values)

    X_copy = X_train.copy()
    outer_len = len(X_copy)
    for file_index in range(20, to_predict):
        df = pd.read_csv(fr"IPF\IPF_{file_index}_pred.csv")
        twenty = df[f"Phi{Euler}"] # Euler can take values 1,_,2

        for i in range(outer_len):
            X_copy[i] = np.delete(X_copy[i], 0)
            X_copy[i] = np.append(X_copy[i], twenty[i])

    path = f"Tension_Phi{Euler}_lstm.h5"
    model = load_model(path)
        
    predicted_values=[]

    for i in range(outer_len):
        pred = model.predict(X_copy[i].reshape(1,18,1))
        predicted_values.append(pred)
        print(i)

        
    predicted_values = np.squeeze(predicted_values, axis=2)
    return predicted_values


In [23]:
# Taking user input for the file_index for which the predictions are to be made
to_predict = int(input("Enter the strain value for which the predictions are to be made: "))

Enter the strain value for which the predictions are to be made: 25


In [18]:
# Making the predictions for the required
Phi1 = predictions(to_predict, 1)

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 187ms/step
0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
2
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
3
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
4
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
5
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
6
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
7
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
11
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
12
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
13
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
14
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
15
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
16
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
17
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
18
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
19
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
20
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
21
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
22
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
23
1/1 ━━━━━━━━━━━━━━━━━━━━ 

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
216
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
217
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
218
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
219
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
220
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 26ms/step
221
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
222
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
223
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
224
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
225
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
226
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step
227
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
228
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
229
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
230
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
231
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
232
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
233
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
234
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
235
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
236
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
237
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
238
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/s

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
430
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
431
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
432
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
433
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
434
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
435
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
436
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
437
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
438
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
439
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
440
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
441
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
442
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
443
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
444
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
445
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
446
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
447
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
448
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
449
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
450
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
451
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
452
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/s

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
644
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
645
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
646
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
647
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
648
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
649
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step
650
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
651
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
652
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
653
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
654
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
655
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
656
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
657
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
658
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
659
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
660
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
661
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
662
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
663
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
664
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
665
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
666
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/s

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
858
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
859
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
860
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
861
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
862
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
863
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
864
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
865
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
866
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
867
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
868
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
869
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
870
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
871
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
872
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
873
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
874
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
875
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
876
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
877
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
878
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
879
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
880
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/s

...

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
9339
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9340
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9341
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9342
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9343
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9344
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9345
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9346
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9347
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
9348
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9349
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9350
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9351
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9352
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9353
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9354
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9355
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9356
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9357
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9358
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9359
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9360
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9361
1/1 ━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9551
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9552
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9553
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9554
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9555
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9556
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9557
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9558
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9559
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9560
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9561
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9562
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9563
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
9564
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9565
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9566
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9567
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9568
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9569
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9570
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9571
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9572
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9573
1/1 ━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9763
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9764
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9765
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9766
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9767
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9768
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9769
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9770
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9771
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9772
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9773
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9774
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9775
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9776
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9777
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9778
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9779
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9780
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9781
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9782
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9783
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9784
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9785
1/1 ━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9975
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9976
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9977
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9978
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9979
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9980
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9981
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9982
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9983
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9984
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9985
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9986
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9987
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
9988
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
9989
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
9990
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
9991
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9992
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
9993
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9994
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9995
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9996
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9997
1/1 ━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10185
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10186
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
10187
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10188
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10189
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10190
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10191
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10192
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10193
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10194
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step
10195
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
10196
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
10197
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
10198
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10199
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10200
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10201
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10202
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10203
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10204
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10205
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
10206
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms

In [19]:
df = pd.DataFrame(Phi1)
df.to_csv(fr"IPF\IPF_{to_predict}_pred.csv")

In [24]:
Phi = predictions(to_predict, "")

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 183ms/step
0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
1
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
2
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
3
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
4
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
5
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
6
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
7
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
11
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
12
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
13
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
14
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
15
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
16
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
17
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
18
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
19
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
20
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
21
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
22
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
23
1/1 ━━━━━━━━━━━━━━━━━━━━ 

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
109
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
110
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
111
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
112
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
113
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
114
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
115
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
116
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
117
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
118
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
119
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
120
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
121
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
122
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
123
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
124
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
125
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
126
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
127
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
128
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
129
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
130
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
131
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/s

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
216
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
217
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
218
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
219
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
220
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
221
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
222
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
223
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
224
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
225
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
226
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
227
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
228
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
229
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
230
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
231
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
232
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
233
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
234
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
235
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
236
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
237
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
238
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/s

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
323
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
324
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
325
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
326
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
327
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
328
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
329
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
330
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
331
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
332
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
333
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
334
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
335
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
336
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
337
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
338
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
339
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
340
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
341
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
342
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
343
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
344
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
345
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/s

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
430
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
431
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
432
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
433
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
434
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
435
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
436
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
437
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
438
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
439
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
440
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
441
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
442
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
443
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
444
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
445
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
446
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
447
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
448
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
449
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
450
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
451
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
452
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/s

...

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9763
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9764
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9765
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9766
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
9767
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9768
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9769
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9770
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9771
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9772
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9773
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9774
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9775
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9776
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9777
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9778
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9779
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9780
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9781
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9782
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9783
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9784
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9785
1/1 ━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
9869
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9870
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9871
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9872
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9873
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9874
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9875
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9876
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9877
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9878
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9879
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9880
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
9881
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9882
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9883
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9884
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9885
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9886
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9887
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9888
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9889
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9890
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9891
1/1 ━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
9975
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9976
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
9977
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9978
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
9979
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
9980
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
9981
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9982
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9983
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
9984
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9985
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
9986
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9987
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9988
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9989
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9990
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9991
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9992
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9993
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9994
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9995
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9996
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9997
1/1 ━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
10080
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
10081
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
10082
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
10083
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10084
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10085
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
10086
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10087
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10088
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10089
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10090
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
10091
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
10092
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10093
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
10094
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10095
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
10096
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10097
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10098
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
10099
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
10100
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10101
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
10185
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10186
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10187
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10188
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10189
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10190
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10191
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10192
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10193
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
10194
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10195
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
10196
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
10197
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10198
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
10199
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10200
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10201
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10202
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
10203
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10204
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10205
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
10206
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms

In [25]:
df = pd.DataFrame(Phi)
df.to_csv(fr"IPF\Phi_{to_predict}_pred.csv")

In [26]:
Phi2 = predictions(to_predict, 2)

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 188ms/step
0
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
1
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
2
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
3
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
4
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
5
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
6
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
7
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step
10
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
11
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
12
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
13
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
14
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
15
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
16
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
17
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
18
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
19
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
20
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
21
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
22
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
23
1/1 ━━━━━━━━━━━━━━━━━━━━ 

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
109
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
110
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
111
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
112
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
113
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
114
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
115
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
116
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
117
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
118
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
119
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
120
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
121
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
122
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
123
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
124
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
125
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
126
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
127
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
128
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
129
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
130
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
131
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/s

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
216
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
217
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
218
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
219
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
220
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
221
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
222
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
223
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
224
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
225
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
226
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
227
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
228
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
229
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
230
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
231
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
232
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
233
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
234
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
235
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
236
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
237
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
238
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/s

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
323
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
324
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
325
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
326
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
327
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
328
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
329
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
330
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
331
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
332
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step
333
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
334
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
335
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
336
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
337
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
338
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
339
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
340
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
341
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
342
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
343
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
344
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
345
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/s

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
430
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
431
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
432
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
433
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
434
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
435
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
436
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
437
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
438
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step
439
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step
440
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
441
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
442
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
443
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
444
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
445
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
446
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
447
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
448
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
449
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
450
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
451
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
452
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/s

...

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
8597
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8598
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
8599
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8600
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8601
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8602
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8603
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8604
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8605
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8606
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8607
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8608
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8609
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8610
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
8611
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8612
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8613
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8614
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8615
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8616
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8617
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8618
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8619
1/1 ━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8703
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8704
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8705
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8706
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8707
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8708
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8709
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8710
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8711
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
8712
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8713
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
8714
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step
8715
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8716
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8717
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8718
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8719
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8720
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8721
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8722
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8723
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8724
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8725
1/1 ━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8809
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8810
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8811
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8812
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8813
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
8814
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8815
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8816
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8817
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8818
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8819
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
8820
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8821
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
8822
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
8823
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
8824
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8825
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8826
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8827
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8828
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8829
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8830
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8831
1/1 ━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step
8915
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8916
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8917
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8918
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8919
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8920
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8921
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8922
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8923
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8924
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8925
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8926
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8927
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8928
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8929
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8930
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8931
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
8932
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
8933
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
8934
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8935
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
8936
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
8937
1/1 ━━━━━━━

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9021
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9022
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9023
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9024
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step
9025
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9026
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9027
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9028
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9029
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9030
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9031
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
9032
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9033
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9034
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9035
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9036
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9037
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9038
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step
9039
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step
9040
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 16ms/step
9041
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9042
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step
9043
1/1 ━━━━━━━

In [27]:
df = pd.DataFrame(Phi2)
df.to_csv(fr"IPF\Phi2_{to_predict}_pred.csv")